# Named Entity Recognition Euro Parliamentary Proceedings

This project involves using Named Entity Recognition to identify prominent entities (dates, persons, organisation, etc.) mentioned within European Parliamentary proceedings corpus. Identifying entities would allow institutions working with European data to access correctly tagged information more quickly than if they were required to browse the full archives for relevant information. The raw dataset can be found on Kaggle at: https://www.kaggle.com/datasets/nltkdata/europarl

This project only features the English documents listed under 'en' in this dataset. However, it may be possible to use other language models to parse information from other translations in the main corpus. The goal is to produce a dataframe that lists individual documents alongside their respective entities.

The project has the following main sections:
- Importing and Preprocessing text files
- Rendering HTML documents labelling entities
- Creating a dataframe listing the entities within each document

## Importing and Preprocessing text files. ##

First, let's import the library using glob.

In [16]:
# Import library
import glob

# The document files are contained in this folder
folder = "C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en/"

# List all the .txt files and sort them alphabetically
files = glob.glob(folder + "*.txt")
files.sort()
files

['C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-01-17.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-01-18.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-01-19.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-01-21.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-02-02.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-02-03.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-02-14.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-02-15.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en\\ep-00-02-16.txt',
 'C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en

NER using Spacy:

Spacy is an open-source Natural Language Processing library that can be used for various tasks. It has built-in methods for Named Entity Recognition. Spacy has a fast statistical entity recognition system.

 We can use spacy very easily for NER tasks. Though often we need to train our own data for business-specific needs, the spacy model general performs well for all types of text data.  

Let us get started with the code, first we import spacy and proceed.

In [17]:
import spacy
from spacy import displacy

# Load the spacy model
NER = spacy.load('en_core_web_sm')

Now, we'll preprocess the text to remove unnecessary characters for a cleaner text dataset.

In [18]:
# Import libraries
import re, os
from tqdm import tqdm

# Initialize the lists that will contain the texts and titles of each document
txts = []
titles = []

for n in tqdm(files):
    # Open each file
    f = open(n, encoding='utf-8-sig')
    # Remove all non-alpha-numeric characters except periods, question marks, exclamation marks. f.read() reads the text and ' ' replaces non-alphanumeric characters with a space.
    data = re.sub('[^a-zA-Z0-9_.?!]+', ' ', f.read())
    # Store the texts and titles of the books in two separate lists
    txts.append(data)
    titles.append(os.path.basename(n).replace(".txt", ""))

# Print the length, in characters, of each text
[len(t) for t in txts]

100%|█████████████████████████████████████████████████████████████████████████████| 9672/9672 [00:16<00:00, 582.29it/s]


[145948,
 554478,
 228562,
 621,
 313588,
 148461,
 170524,
 567212,
 539039,
 372335,
 87525,
 429773,
 111212,
 238353,
 563837,
 420292,
 372870,
 83035,
 384564,
 150722,
 193923,
 566629,
 591732,
 388809,
 135977,
 363042,
 101234,
 164713,
 522362,
 530154,
 390793,
 97827,
 547326,
 555861,
 417767,
 127854,
 222818,
 604146,
 635509,
 485768,
 76406,
 195047,
 511347,
 575239,
 348038,
 54431,
 341393,
 169268,
 168962,
 506804,
 550622,
 287524,
 35246,
 193550,
 606175,
 618492,
 224323,
 85354,
 134872,
 550435,
 577608,
 319132,
 98021,
 422050,
 242698,
 180388,
 545028,
 531340,
 311981,
 86759,
 139786,
 531481,
 570621,
 280861,
 401894,
 159915,
 160314,
 562344,
 551183,
 350538,
 363830,
 155890,
 231300,
 550907,
 548066,
 291110,
 165327,
 531114,
 542866,
 332370,
 364461,
 154168,
 163325,
 558401,
 515606,
 357277,
 387763,
 193118,
 179780,
 530585,
 501422,
 308997,
 130008,
 499067,
 626885,
 317690,
 228123,
 608609,
 644135,
 352357,
 46968,
 356053,
 1513

The titles of each document will be converted to a dataframe column. This column can be used as an index to identify each document and its respective entities in the final dataframe.

In [19]:
import pandas as pd

In [21]:
title_dataframe = pd.DataFrame(titles)
title_dataframe.rename(columns = {0 : 'File_Name'}, inplace = True)

This dataframe will be used to indicate the filename in the final table.

In [22]:
title_dataframe.head(10)

File_Name
0  ep-00-01-17
1  ep-00-01-18
2  ep-00-01-19
3  ep-00-01-21
4  ep-00-02-02
5  ep-00-02-03
6  ep-00-02-14
7  ep-00-02-15
8  ep-00-02-16
9  ep-00-02-17

## Rendering HTML documents labelling entities ##

In the next section, we'll render html documents clearly highlighting entities within the documents themselves. This should allow a reader to quickly scan a given document in the corpus and see what entities have been tagged. (It should be noted that some documents may be short enough that no entities are discovered.)

In [24]:
from pathlib import Path

for i, t in tqdm(zip(titles, txts)): 
    text= NER(t)
    # Creates an html render for each document highlighting the location of known entities.
    html = displacy.render(text, style="ent", jupyter=False)
    # The filename for each document will be created using the titles list created earlier.
    file_name = i + ".html"
    with open("C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en/Renders/" + file_name, 'w+', encoding="utf-8") as fp:
        fp.write(html)
        fp.close()
#    output_path = Path("C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en/Preprocessing_Sample/Renders/" + file_name)
#    output_path.open("w", encoding="utf-8").write(svg)


432it [36:02,  2.82it/s]C:\Users\dalin\anaconda3\envs\Summarization_Entity_Recog\lib\site-packages\spacy\displacy\__init__.py:205: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)
9672it [1:26:25,  1.87it/s] 


## Creating a dataframe listing the entities within each document ##

Now we will generate a dataframe that adds each document's entities as a new row. The final dataframe can be used as a database to identify the location of prominent entites within the Euro Parl corpus.

In [25]:
df = pd.DataFrame()
for t in tqdm(txts):
    text= NER(t)
    entity_list = []
    for word in text.ents:
        word_label = (word.text, word.label_)
        entity_list.append(word_label)
    df = df.append(pd.DataFrame([entity_list]))

  0%|                                                                                         | 0/9672 [00:00<?, ?it/s]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  0%|                                                                              | 3/9672 [00:14<12:49:26,  4.77s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  0%|                   

  0%|▏                                                                            | 25/9672 [01:57<13:15:35,  4.95s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  0%|▏                                                                            | 26/9672 [02:03<13:40:32,  5.10s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  0%|▏                                                                            | 27/9672 [02:04<10:46:32,  4.02s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

  0%|▍                                                                            | 48/9672 [03:59<10:50:13,  4.05s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▍                                                                             | 49/9672 [04:01<9:38:01,  3.60s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▍                                                                            | 50/9672 [04:09<12:54:41,  4.83s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

  1%|▌                                                                             | 71/9672 [05:51<9:54:51,  3.72s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▌                                                                            | 72/9672 [05:59<13:19:40,  5.00s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▌                                                                            | 73/9672 [06:08<16:14:31,  6.09s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

  1%|▋                                                                            | 94/9672 [08:00<14:14:08,  5.35s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▊                                                                            | 95/9672 [08:08<16:08:01,  6.06s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
  1%|▊                                                                            | 96/9672 [08:13<15:31:27,  5.84s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

...

 99%|███████████████████████████████████████████████████████████████████████████▏| 9563/9672 [1:45:29<09:32,  5.25s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▏| 9564/9672 [1:45:38<11:46,  6.55s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▏| 9565/9672 [1:45:44<11:23,  6.39s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

 99%|███████████████████████████████████████████████████████████████████████████▎| 9586/9672 [1:47:27<05:39,  3.95s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▎| 9587/9672 [1:47:35<07:29,  5.29s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▎| 9588/9672 [1:47:43<08:24,  6.01s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

 99%|███████████████████████████████████████████████████████████████████████████▌| 9609/9672 [1:49:22<04:45,  4.53s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▌| 9610/9672 [1:49:25<03:58,  3.85s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
 99%|███████████████████████████████████████████████████████████████████████████▌| 9611/9672 [1:49:33<05:20,  5.25s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

100%|███████████████████████████████████████████████████████████████████████████▋| 9632/9672 [1:51:22<03:27,  5.19s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
100%|███████████████████████████████████████████████████████████████████████████▋| 9633/9672 [1:51:30<04:01,  6.19s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
100%|███████████████████████████████████████████████████████████████████████████▋| 9634/9672 [1:51:36<03:54,  6.17s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

100%|███████████████████████████████████████████████████████████████████████████▊| 9655/9672 [1:53:04<01:11,  4.23s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
100%|███████████████████████████████████████████████████████████████████████████▊| 9656/9672 [1:53:11<01:22,  5.14s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame([entity_list]))
100%|███████████████████████████████████████████████████████████████████████████▉| 9657/9672 [1:53:15<01:09,  4.62s/it]C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\4142217014.py:8: FutureWarning: The frame.append method is deprecated and will be removed from pandas

This process will generate an extra index column that we do not need, so this can be dropped.

In [26]:
df.reset_index(inplace = True)

df.head()

C:\Users\dalin\AppData\Local\Temp\ipykernel_12280\1576094960.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df.reset_index(inplace = True)


index                  0                               1  \
0      0      (1, CARDINAL)  (the European Parliament, ORG)   
1      0      (1, CARDINAL)           (The Minutes, PERSON)   
2      0  (CHAPTER ID, ORG)                   (5, CARDINAL)   
3      0     (12, CARDINAL)             (Fraga Est, PERSON)   
4      0      (1, CARDINAL)  (the European Parliament, ORG)   

                                 2                          3  \
0  (Friday 17 December 1999, DATE)  (the next few days, DATE)   
1                (yesterday, DATE)              (2, CARDINAL)   
2               (Middle East, LOC)             (80, CARDINAL)   
3             (this morning, TIME)              (Madrid, GPE)   
4   (Friday 21 January 2000, DATE)     (Angelilli Madam, ORG)   

                                   4                    5  \
0          (the European Union, ORG)  (this minute, TIME)   
1                  (yesterday, DATE)    (afternoon, TIME)   
2  (the Council and Commission, ORG)   (Middle East, LOC)   
3                    (one, CARDINAL)       (13, CARDINAL)   
4                  (second, ORDINAL)        (Cermis, ORG)   

                         6                                     7  \
0             (House, ORG)                         (2, CARDINAL)   
1             (House, ORG)                    (Minutes, PRODUCT)   
2           (81, CARDINAL)  (the Council for the statement, ORG)   
3  (Mrs Fraga Est, PERSON)                       (Spanish, NORP)   
4    (Two years ago, DATE)                      (Cavalese, NORP)   

                      8  ... 6701 6702 6703 6704 6705 6706 6707 6708 6709 6710  
0      (Sri Lanka, GPE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
1        (11, CARDINAL)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
2  (this morning, TIME)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
3   (Spanish, LANGUAGE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
4          (Italy, GPE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 6712 columns]

In [ ]:
# Drop the extra index column
del df[df.columns[0]]

Join title dataframe and entity dataframe together so that the title of each document fills the first column under "File_Name".

In [28]:
main_data = title_dataframe.join(df)
main_data.head()

File_Name                  0                               1  \
0  ep-00-01-17      (1, CARDINAL)  (the European Parliament, ORG)   
1  ep-00-01-18      (1, CARDINAL)           (The Minutes, PERSON)   
2  ep-00-01-19  (CHAPTER ID, ORG)                   (5, CARDINAL)   
3  ep-00-01-21     (12, CARDINAL)             (Fraga Est, PERSON)   
4  ep-00-02-02      (1, CARDINAL)  (the European Parliament, ORG)   

                                 2                          3  \
0  (Friday 17 December 1999, DATE)  (the next few days, DATE)   
1                (yesterday, DATE)              (2, CARDINAL)   
2               (Middle East, LOC)             (80, CARDINAL)   
3             (this morning, TIME)              (Madrid, GPE)   
4   (Friday 21 January 2000, DATE)     (Angelilli Madam, ORG)   

                                   4                    5  \
0          (the European Union, ORG)  (this minute, TIME)   
1                  (yesterday, DATE)    (afternoon, TIME)   
2  (the Council and Commission, ORG)   (Middle East, LOC)   
3                    (one, CARDINAL)       (13, CARDINAL)   
4                  (second, ORDINAL)        (Cermis, ORG)   

                         6                                     7  \
0             (House, ORG)                         (2, CARDINAL)   
1             (House, ORG)                    (Minutes, PRODUCT)   
2           (81, CARDINAL)  (the Council for the statement, ORG)   
3  (Mrs Fraga Est, PERSON)                       (Spanish, NORP)   
4    (Two years ago, DATE)                      (Cavalese, NORP)   

                      8  ... 6701 6702 6703 6704 6705 6706 6707 6708 6709 6710  
0      (Sri Lanka, GPE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
1        (11, CARDINAL)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
2  (this morning, TIME)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
3   (Spanish, LANGUAGE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
4          (Italy, GPE)  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 6712 columns]

This dataframe can be further summarized info a final dataframe that lists how many times each entity appears in each document. This method will generate a sparse matrix that can be used to locate the importance of an entity within each document.

In [29]:
summary_data = df.apply(pd.value_counts, axis=1)
summary_data.head()

0      0 0124 96 0 0145 96 0 3 years  0 5 0 5 million euro 0 96 0249  \
  CARDINAL DATE      DATE      DATE      DATE DATE            MONEY  CARDINAL   
0      NaN  NaN       NaN       NaN       NaN  NaN              NaN       NaN   
1      NaN  NaN       NaN       NaN       NaN  NaN              NaN       NaN   
2      NaN  NaN       NaN       NaN       NaN  NaN              NaN       NaN   
3      NaN  NaN       NaN       NaN       NaN  NaN              NaN       NaN   
4      NaN  NaN       NaN       NaN       NaN  NaN              NaN       NaN   

  0 francs 0 million  ... zobacz protok zoos          zosta   zsef zsef B  \
     MONEY  CARDINAL  ...        PERSON DATE PERSON PRODUCT PERSON PERSON   
0      NaN       NaN  ...           NaN  NaN    NaN     NaN    NaN    NaN   
1      NaN       NaN  ...           NaN  NaN    NaN     NaN    NaN    NaN   
2      NaN       NaN  ...           NaN  NaN    NaN     NaN    NaN    NaN   
3      NaN       NaN  ...           NaN  NaN    NaN     NaN    NaN    NaN   
4      NaN       NaN  ...           NaN  NaN    NaN     NaN    NaN    NaN   

  zsef Kasza zsef PPE DE   zuen zuri  
      PERSON      PERSON PERSON  GPE  
0        NaN         NaN    NaN  NaN  
1        NaN         NaN    NaN  NaN  
2        NaN         NaN    NaN  NaN  
3        NaN         NaN    NaN  NaN  
4        NaN         NaN    NaN  NaN  

[5 rows x 184560 columns]

Add the document titles back to this dataframe as the first column.

In [ ]:
final_data = title_dataframe.join(summary_data)

Save Table as a .csv file.

In [31]:
final_data.to_csv("C:/Users/dalin/Dropbox/MachineLearning/Entity Recognition/Euro_Parliament/txt/en/Entity_list.csv")